In [ ]:
import pandas as pd
import numpy as np
import chardet
from pathlib import Path
import json
import ast
import os
from skimage.transform import resize
from sklearn.preprocessing import OneHotEncoder
from sklearn.feature_extraction.text import TfidfVectorizer
import cv2
import hashlib

In [ ]:
from google.colab import data_table

# data_table.enable_dataframe_formatter()

In [83]:
with open('/content/drive/MyDrive/DefeatedURansom/Updated_Samples_23_features.csv', 'rb') as f:
    result = chardet.detect(f.read())  # or readline if the file is large


ransom_df = pd.read_csv('/content/drive/MyDrive/DefeatedURansom/Updated_Samples_23_features.csv', encoding=result['encoding'])


ransom_df.head(10)

generic  \
0  [{'process_path': 'C:\\Users\\Administrator\\A...   
1  [{'process_path': 'C:\\Windows\\System32\\lsas...   
2  [{'process_path': 'C:\\Users\\Administrator\\A...   
3  [{'process_path': 'C:\\Windows\\System32\\lsas...   
4  [{'process_path': 'C:\\Users\\Administrator\\A...   
5  [{'process_path': 'C:\\Windows\\System32\\lsas...   
6  [{'process_path': 'C:\\Windows\\SysWOW64\\cmd....   
7  [{'process_path': 'C:\\Users\\Administrator\\A...   
8  [{'process_path': 'C:\\Users\\Administrator\\A...   

                                            apistats  \
0  {'664': {'CreateToolhelp32Snapshot': 1, 'LdrUn...   
1                                                 {}   
2  {'1756': {'GetNativeSystemInfo': 1, 'DeviceIoC...   
3  {'2424': {'LdrUnloadDll': 2, 'DeviceIoControl'...   
4  {'2684': {'GetForegroundWindow': 8, 'NtAllocat...   
5  {'2836': {'LdrUnloadDll': 3, 'CoUninitialize':...   
6  {'2316': {'NtDuplicateObject': 1, 'DeviceIoCon...   
7  {'2232': {'NtDuplicateObject': 7, 'LdrUnloadDl...   
8  {'800': {'LdrUnloadDll': 1, 'NtDeviceIoControl...   

                                           processes  \
0  [{'process_path': 'C:\\Windows\\System32\\lsas...   
1  [{'process_path': 'C:\\Windows\\System32\\lsas...   
2  [{'process_path': 'C:\\Windows\\System32\\lsas...   
3  [{'process_path': 'C:\\Windows\\System32\\lsas...   
4  [{'process_path': 'C:\\Windows\\System32\\lsas...   
5  [{'process_path': 'C:\\Windows\\System32\\lsas...   
6  [{'process_path': 'C:\\Windows\\System32\\lsas...   
7  [{'process_path': 'C:\\Windows\\System32\\lsas...   
8  [{'process_path': 'C:\\Windows\\System32\\lsas...   

                                         processtree  \
0  [{'track': False, 'pid': 516, 'process_name': ...   
1  [{'track': False, 'pid': 504, 'process_name': ...   
2  [{'track': False, 'pid': 516, 'process_name': ...   
3  [{'track': False, 'pid': 512, 'process_name': ...   
4  [{'track': False, 'pid': 508, 'process_name': ...   
5  [{'track': False, 'pid': 504, 'process_name': ...   
6  [{'track': False, 'pid': 508, 'process_name': ...   
7  [{'track': False, 'pid': 508, 'process_name': ...   
8  [{'track': False, 'pid': 500, 'process_name': ...   

                                             summary Directory_Label  
0  {'regkey_read': ['HKEY_LOCAL_MACHINE\\SOFTWARE...           8Base  
1                                                 {}        BianLian  
2  {'file_created': ['C:\\Users\\Administrator\\D...      BlackBasta  
3  {'file_recreated': ['\\Device\\KsecDD'], 'regk...        BlackCat  
4  {'regkey_read': ['HKEY_LOCAL_MACHINE\\SYSTEM\\...            CL0P  
5  {'file_recreated': ['\\??\\MountPointManager']...    MedusaLocker  
6  {'file_recreated': ['\\Device\\KsecDD'], 'regk...        NoEscape  
7  {'dll_loaded': ['kernel32', 'api-ms-win-core-l...            Play  
8  {'file_opened': ['C:\\Windows\\System32\\en-US...           Royal

In [ ]:
ransom_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 9 entries, 0 to 8
Data columns (total 6 columns):
 #   Column           Non-Null Count  Dtype 
---  ------           --------------  ----- 
 0   generic          9 non-null      object
 1   apistats         9 non-null      object
 2   processes        9 non-null      object
 3   processtree      9 non-null      object
 4   summary          9 non-null      object
 5   Directory_Label  9 non-null      object
dtypes: object(6)
memory usage: 560.0+ bytes


## Generic Data

In [ ]:
json.dumps({'data':''})
ransom_df['generic'] = ransom_df['generic'].replace('"C:','^').replace("'",'"').replace(" False",'"false"').replace(" True",'"true"').replace(' ",',",").replace("\\","/")

In [ ]:
ransom_df

generic  \
0  [{'process_path': 'C:\\Users\\Administrator\\A...   
1  [{'process_path': 'C:\\Windows\\System32\\lsas...   
2  [{'process_path': 'C:\\Users\\Administrator\\A...   
3  [{'process_path': 'C:\\Windows\\System32\\lsas...   
4  [{'process_path': 'C:\\Users\\Administrator\\A...   
5  [{'process_path': 'C:\\Windows\\System32\\lsas...   
6  [{'process_path': 'C:\\Windows\\SysWOW64\\cmd....   
7  [{'process_path': 'C:\\Users\\Administrator\\A...   
8  [{'process_path': 'C:\\Users\\Administrator\\A...   

                                            apistats  \
0  {'664': {'CreateToolhelp32Snapshot': 1, 'LdrUn...   
1                                                 {}   
2  {'1756': {'GetNativeSystemInfo': 1, 'DeviceIoC...   
3  {'2424': {'LdrUnloadDll': 2, 'DeviceIoControl'...   
4  {'2684': {'GetForegroundWindow': 8, 'NtAllocat...   
5  {'2836': {'LdrUnloadDll': 3, 'CoUninitialize':...   
6  {'2316': {'NtDuplicateObject': 1, 'DeviceIoCon...   
7  {'2232': {'NtDuplicateObject': 7, 'LdrUnloadDl...   
8  {'800': {'LdrUnloadDll': 1, 'NtDeviceIoControl...   

                                           processes  \
0  [{'process_path': 'C:\\Windows\\System32\\lsas...   
1  [{'process_path': 'C:\\Windows\\System32\\lsas...   
2  [{'process_path': 'C:\\Windows\\System32\\lsas...   
3  [{'process_path': 'C:\\Windows\\System32\\lsas...   
4  [{'process_path': 'C:\\Windows\\System32\\lsas...   
5  [{'process_path': 'C:\\Windows\\System32\\lsas...   
6  [{'process_path': 'C:\\Windows\\System32\\lsas...   
7  [{'process_path': 'C:\\Windows\\System32\\lsas...   
8  [{'process_path': 'C:\\Windows\\System32\\lsas...   

                                         processtree  \
0  [{'track': False, 'pid': 516, 'process_name': ...   
1  [{'track': False, 'pid': 504, 'process_name': ...   
2  [{'track': False, 'pid': 516, 'process_name': ...   
3  [{'track': False, 'pid': 512, 'process_name': ...   
4  [{'track': False, 'pid': 508, 'process_name': ...   
5  [{'track': False, 'pid': 504, 'process_name': ...   
6  [{'track': False, 'pid': 508, 'process_name': ...   
7  [{'track': False, 'pid': 508, 'process_name': ...   
8  [{'track': False, 'pid': 500, 'process_name': ...   

                                             summary Directory_Label  
0  {'regkey_read': ['HKEY_LOCAL_MACHINE\\SOFTWARE...           8Base  
1                                                 {}        BianLian  
2  {'file_created': ['C:\\Users\\Administrator\\D...      BlackBasta  
3  {'file_recreated': ['\\Device\\KsecDD'], 'regk...        BlackCat  
4  {'regkey_read': ['HKEY_LOCAL_MACHINE\\SYSTEM\\...            CL0P  
5  {'file_recreated': ['\\??\\MountPointManager']...    MedusaLocker  
6  {'file_recreated': ['\\Device\\KsecDD'], 'regk...        NoEscape  
7  {'dll_loaded': ['kernel32', 'api-ms-win-core-l...            Play  
8  {'file_opened': ['C:\\Windows\\System32\\en-US...           Royal

### Extraction

In [ ]:
# def process_generic(data):
#         if data == "{}":
#                 return json.dumps({'data':''})

#         datax = data.replace('"C:','^').replace("'",'"').replace(" False",'"false"').replace(" True",'"true"').replace("^",'C:').replace(' ",',",").replace("\\","/")
#         data = json.loads(datax)
#         process_data = {}


### Transformation

In [ ]:
gen_outputs = []
vectorizer = TfidfVectorizer(stop_words=None)
for raw_data in ransom_df['generic'].values:
    raw_vector = vectorizer.fit_transform([raw_data]).toarray()
    gen_outputs.append(raw_vector)


# for index,raw in enumerate(ransom_df['generic'].values):
#     #print(raw[0])
#     #print(process_tree_preprocessing(raw[0]))
#     # raw_processing_data = process_summary(raw[1])
#     # print('output',raw_processing_data)
#     #print('epoch',index)
#     raw_vector = vectorizer.fit_transform([raw_processing_data]).toarray()
#     outputs.append(raw_vector)


In [ ]:
gen_outputs

[array([[0.11111111, 0.11111111, 0.11111111, 0.11111111, 0.11111111,
         0.11111111, 0.22222222, 0.11111111, 0.11111111, 0.11111111,
         0.11111111, 0.11111111, 0.11111111, 0.22222222, 0.11111111,
         0.44444444, 0.22222222, 0.11111111, 0.11111111, 0.11111111,
         0.11111111, 0.22222222, 0.11111111, 0.11111111, 0.11111111,
         0.22222222, 0.22222222, 0.22222222, 0.22222222, 0.11111111,
         0.11111111, 0.22222222, 0.11111111, 0.11111111, 0.11111111,
         0.22222222]]),
 array([[0.2236068, 0.2236068, 0.2236068, 0.2236068, 0.4472136, 0.2236068,
         0.4472136, 0.2236068, 0.2236068, 0.2236068, 0.2236068, 0.2236068,
         0.2236068, 0.2236068]]),
 array([[0.00110707, 0.00081574, 0.0056519 , ..., 0.00011653, 0.00011653,
         0.00011653]]),
 array([[0.14865883, 0.07432941, 0.07432941, 0.07432941, 0.07432941,
         0.07432941, 0.07432941, 0.07432941, 0.07432941, 0.07432941,
         0.07432941, 0.07432941, 0.29731766, 0.29731766, 0.07432941,
    

In [54]:
import cv2
import numpy as np

# Function to create grayscale image from array
def create_grayscale_image(array, image_shape=(28, 28)):
    # Resize array to match image dimensions
    resized_array = cv2.resize(array, image_shape[::-1])

    # Normalize array values between 0 and 255
    normalized_array = ((resized_array - resized_array.min()) / (resized_array.max() - resized_array.min())) * 255

    # Convert to uint8
    image_data = normalized_array.astype(np.uint8)

    return image_data

# Directory to store the images
output_folder = "generic_images"
os.makedirs(output_folder, exist_ok=True)

# Iterate over each array in gen_outputs
for i, array in enumerate(gen_outputs):
    # Create grayscale image from array
    image_data = create_grayscale_image(array)

    # Save image as PNG file
    filename = os.path.join(output_folder, f"generic_image_{i}.png")
    cv2.imwrite(filename, image_data)
    print(f"Image saved: {filename}")


Image saved: generic_images/generic_image_0.png
Image saved: generic_images/generic_image_1.png
Image saved: generic_images/generic_image_2.png
Image saved: generic_images/generic_image_3.png
Image saved: generic_images/generic_image_4.png
Image saved: generic_images/generic_image_5.png
Image saved: generic_images/generic_image_6.png
Image saved: generic_images/generic_image_7.png
Image saved: generic_images/generic_image_8.png


Image saved: combined_images/combined_image_0.png
Image saved: combined_images/combined_image_1.png
Image saved: combined_images/combined_image_2.png
Image saved: combined_images/combined_image_3.png
Image saved: combined_images/combined_image_4.png
Image saved: combined_images/combined_image_5.png
Image saved: combined_images/combined_image_6.png
Image saved: combined_images/combined_image_7.png
Image saved: combined_images/combined_image_8.png


## API-Stats Data

In [103]:
apistats_data = ransom_df["apistats"]

apistats_data[3]

"{'2424': {'LdrUnloadDll': 2, 'DeviceIoControl': 1, 'LdrGetDllHandle': 11, 'NtAllocateVirtualMemory': 1, 'RtlAddVectoredExceptionHandler': 1, 'CreateThread': 1, 'GetFileInformationByHandleEx': 1, 'NtOpenKey': 15, 'LdrGetProcedureAddress': 6, 'SetUnhandledExceptionFilter': 1, 'NtDeviceIoControlFile': 5, 'NtQueryValueKey': 11, 'GetSystemTimeAsFileTime': 1, 'NtOpenFile': 1, 'LdrLoadDll': 1, 'GetSystemWindowsDirectoryW': 2, 'NtTerminateProcess': 3, 'NtProtectVirtualMemory': 2, 'GetSystemInfo': 1, 'NtClose': 25}}"

### Extraction

In [104]:
# Extract unique API call names
api_call_names = set()
for sample in apistats_data:
    sample_data = ast.literal_eval(sample) if isinstance(sample, str) else sample
    for inner_dict in sample_data.values():
        api_call_names.update(inner_dict.keys())

# Create a mapping from API call names to indices
api_call_to_index = {api_call: index for index, api_call in enumerate(api_call_names)}

### Transformation

In [105]:
def prepare_apistats_feature(apistats_data, api_call_to_index):
    """
    Prepares API statistics data for feature extraction.

    Args:
        apistats_data (dict or str): Dictionary or string representation of API call counts.
        api_call_to_index (dict): Mapping from API call names to indices.

    Returns:
        numpy.ndarray: Feature vector representing normalized API call frequencies.
    """
    # Convert string representation to dictionary if necessary
    if isinstance(apistats_data, str):
        try:
            apistats_data = ast.literal_eval(apistats_data)
        except (ValueError, SyntaxError):
            # Handle invalid string representation
            return np.zeros(len(api_call_to_index))

    # Initialize feature vector
    feature_vector = np.zeros(len(api_call_to_index))

    # Populate feature vector
    for inner_dict in apistats_data.values():
        for api_call, count in inner_dict.items():
            if api_call in api_call_to_index:
                index = api_call_to_index[api_call]
                feature_vector[index] += count

    # Normalize feature vector
    feature_vector /= feature_vector.sum()

    return feature_vector

In [106]:
# Prepare feature vectors for each sample and store them in a DataFrame
feature_vectors = [prepare_apistats_feature(sample, api_call_to_index) for sample in apistats_data]


<ipython-input-105-d60a5ee6d64e>:31: RuntimeWarning: divide by zero encountered in divide
  feature_vector /= feature_vector.sum()
<ipython-input-105-d60a5ee6d64e>:31: RuntimeWarning: invalid value encountered in divide
  feature_vector /= feature_vector.sum()


In [107]:
api_features = pd.DataFrame(feature_vectors, columns=list(api_call_names))

api_features.head()

LdrUnloadDll  CoUninitialize  DeviceIoControl  FindFirstFileExW  \
0      0.000096             0.0         0.000000          0.000000   
1           NaN             NaN              NaN               NaN   
2      0.000000             0.0         0.000585          0.003382   
3      0.021739             0.0         0.010870          0.000000   
4      0.000000             0.0         0.000000          0.000000   

   CoGetClassObject  WriteConsoleA  GetTimeZoneInformation  UuidCreate  \
0               0.0       0.000000                     0.0         0.0   
1               NaN            NaN                     NaN         NaN   
2               0.0       0.003818                     0.0         0.0   
3               0.0       0.000000                     0.0         0.0   
4               0.0       0.000000                     0.0         0.0   

   RegQueryValueExA  CoInitializeSecurity  ...  NtEnumerateKey  \
0               0.0                   0.0  ...        0.000000   
1               NaN                   NaN  ...             NaN   
2               0.0                   0.0  ...        0.000006   
3               0.0                   0.0  ...        0.000000   
4               0.0                   0.0  ...        0.000000   

   RegCreateKeyExW  SetFileAttributesW  CreateActCtxW  NtOpenFile  NtReadFile  \
0              0.0                 0.0            0.0    0.000000    0.000000   
1              NaN                 NaN            NaN         NaN         NaN   
2              0.0                 0.0            0.0    0.000008    0.156899   
3              0.0                 0.0            0.0    0.010870    0.000000   
4              0.0                 0.0            0.0    0.000000    0.000000   

   NtMapViewOfSection  LdrLoadDll  NtCreateSection  GetForegroundWindow  
0            0.000000    0.875300         0.000000             0.000000  
1                 NaN         NaN              NaN                  NaN  
2            0.000006    0.000042         0.000003             0.000000  
3            0.000000    0.010870         0.000000             0.000000  
4            0.000000    0.152174         0.000000             0.173913  

[5 rows x 110 columns]

In [108]:
print(api_features.isnull().sum())

print('\n Nunber of NaN values:',api_features.isnull().sum().sum())

LdrUnloadDll           1
CoUninitialize         1
DeviceIoControl        1
FindFirstFileExW       1
CoGetClassObject       1
                      ..
NtReadFile             1
NtMapViewOfSection     1
LdrLoadDll             1
NtCreateSection        1
GetForegroundWindow    1
Length: 110, dtype: int64

 Nunber of NaN values: 110


In [109]:
# Impute Missing Values
api_features.fillna(0, inplace=True)


# from sklearn.experimental import enable_iterative_imputer
# from sklearn.impute import IterativeImputer
# from numpy import isnan


# values = api_features.values

# # define the imputer
# imputer = IterativeImputer(random_state=0)

# # transform the dataset
# transformed_values = imputer.fit_transform(values)

# # count the number of NaN values in each column
# print(f'Missing: {isnan(transformed_values).sum()}')


In [110]:
api_features.head()

LdrUnloadDll  CoUninitialize  DeviceIoControl  FindFirstFileExW  \
0      0.000096             0.0         0.000000          0.000000   
1      0.000000             0.0         0.000000          0.000000   
2      0.000000             0.0         0.000585          0.003382   
3      0.021739             0.0         0.010870          0.000000   
4      0.000000             0.0         0.000000          0.000000   

   CoGetClassObject  WriteConsoleA  GetTimeZoneInformation  UuidCreate  \
0               0.0       0.000000                     0.0         0.0   
1               0.0       0.000000                     0.0         0.0   
2               0.0       0.003818                     0.0         0.0   
3               0.0       0.000000                     0.0         0.0   
4               0.0       0.000000                     0.0         0.0   

   RegQueryValueExA  CoInitializeSecurity  ...  NtEnumerateKey  \
0               0.0                   0.0  ...        0.000000   
1               0.0                   0.0  ...        0.000000   
2               0.0                   0.0  ...        0.000006   
3               0.0                   0.0  ...        0.000000   
4               0.0                   0.0  ...        0.000000   

   RegCreateKeyExW  SetFileAttributesW  CreateActCtxW  NtOpenFile  NtReadFile  \
0              0.0                 0.0            0.0    0.000000    0.000000   
1              0.0                 0.0            0.0    0.000000    0.000000   
2              0.0                 0.0            0.0    0.000008    0.156899   
3              0.0                 0.0            0.0    0.010870    0.000000   
4              0.0                 0.0            0.0    0.000000    0.000000   

   NtMapViewOfSection  LdrLoadDll  NtCreateSection  GetForegroundWindow  
0            0.000000    0.875300         0.000000             0.000000  
1            0.000000    0.000000         0.000000             0.000000  
2            0.000006    0.000042         0.000003             0.000000  
3            0.000000    0.010870         0.000000             0.000000  
4            0.000000    0.152174         0.000000             0.173913  

[5 rows x 110 columns]

In [111]:
api_features.isnull().sum()

LdrUnloadDll           0
CoUninitialize         0
DeviceIoControl        0
FindFirstFileExW       0
CoGetClassObject       0
                      ..
NtReadFile             0
NtMapViewOfSection     0
LdrLoadDll             0
NtCreateSection        0
GetForegroundWindow    0
Length: 110, dtype: int64

### TF-IDF

In [122]:
ransom_df['apistats'][1] = ransom_df['apistats'][1].replace('{}', '{NAN}')
ransom_df['apistats']

0    {'664': {'CreateToolhelp32Snapshot': 1, 'LdrUn...
1                                                {NAN}
2    {'1756': {'GetNativeSystemInfo': 1, 'DeviceIoC...
3    {'2424': {'LdrUnloadDll': 2, 'DeviceIoControl'...
4    {'2684': {'GetForegroundWindow': 8, 'NtAllocat...
5    {'2836': {'LdrUnloadDll': 3, 'CoUninitialize':...
6    {'2316': {'NtDuplicateObject': 1, 'DeviceIoCon...
7    {'2232': {'NtDuplicateObject': 7, 'LdrUnloadDl...
8    {'800': {'LdrUnloadDll': 1, 'NtDeviceIoControl...
Name: apistats, dtype: object

In [123]:
apiStats_outputs = []
vectorizer = TfidfVectorizer(stop_words=None)
for raw_data in ransom_df['apistats'].values:
    raw_vector = vectorizer.fit_transform([raw_data]).toarray()
    apiStats_outputs.append(raw_vector)


In [124]:
apiStats_outputs

[array([[0.21320072, 0.21320072, 0.21320072, 0.21320072, 0.21320072,
         0.21320072, 0.21320072, 0.21320072, 0.21320072, 0.21320072,
         0.21320072, 0.21320072, 0.21320072, 0.21320072, 0.21320072,
         0.21320072, 0.21320072, 0.21320072, 0.21320072, 0.21320072,
         0.21320072, 0.21320072]]),
 array([[1.]]),
 array([[0.13245324, 0.13245324, 0.13245324, 0.13245324, 0.13245324,
         0.13245324, 0.13245324, 0.13245324, 0.13245324, 0.13245324,
         0.13245324, 0.13245324, 0.13245324, 0.13245324, 0.13245324,
         0.13245324, 0.13245324, 0.13245324, 0.13245324, 0.13245324,
         0.13245324, 0.13245324, 0.13245324, 0.13245324, 0.13245324,
         0.13245324, 0.13245324, 0.13245324, 0.13245324, 0.13245324,
         0.13245324, 0.13245324, 0.13245324, 0.13245324, 0.13245324,
         0.13245324, 0.13245324, 0.13245324, 0.13245324, 0.13245324,
         0.13245324, 0.13245324, 0.13245324, 0.13245324, 0.13245324,
         0.13245324, 0.13245324, 0.13245324, 0.1324

## Processes Data

### Extraction

In [ ]:
processes_sample = ransom_df['processes'][1]

In [ ]:
# Define a function to apply replacements and extract JSON data from each row
processes_sample = processes_sample.replace('C:', '^').replace("'", '"').replace(" False", "false").replace(" True", '"true"').replace(' ",', ",").replace("\\", "/").replace(" .", "/")


In [ ]:
def extract_process_data(json_str):
    """
    Extracts process data from a JSON string, handling potential errors and providing descriptive output.

    Args:
        json_str (str): The JSON string containing process data.

    Returns:
        dict or None: A dictionary containing extracted data or None if parsing fails.
        list: A list of informative error messages encountered during parsing (if any).

    Raises:
        ValueError: If invalid data types are encountered in the JSON structure.
    """
    errors = []
    try:
        data = json.loads(json_str)
        if not isinstance(data, list):
            raise ValueError("Expected a list of process data.")

        extracted_data = []
        for process in data:
            if not isinstance(process, dict):
                errors.append("Invalid process data format: {}".format(process))
                continue

            extracted_data.append({
                # 'id': process.get('pid', 0),  # Assuming 'id' corresponds to PID
                'process_path': process.get('process_path', ''),
                'pid': process.get('pid', 0),
                'process_name': process.get('process_name', ''),
                'track': process.get('track', False),
                'command_line': process.get('command_line', ''),
                'time': process.get('time', 0),
                'tid': process.get('tid', 0),
                'first_seen': process.get('first_seen', 0),
                'ppid': process.get('ppid', 0),
                'type': process.get('type', ''),
                # Extract additional features from 'modules' and other fields
                'modules': extract_module_data(process.get('modules', [])),
                'calls': extract_call_data(process.get('calls', [])),
            })

        return extracted_data, errors
    except json.JSONDecodeError as e:
        errors.append(f"Error decoding JSON data: {e}")
        return None, errors

In [ ]:
def extract_module_data(modules):
    """
    Extracts data from a list of module dictionaries.

    Args:
        modules (list): A list of dictionaries containing module information.

    Returns:
        list: A list of dictionaries containing extracted module data.
    """
    extracted_modules = []
    for module in modules:
        if not isinstance(module, dict):
            continue  # Skip invalid modules
        extracted_modules.append({
            'basename': module.get('basename', ''),
            'imgsize': module.get('imgsize', 0),
            # Extract additional features from module data (e.g., file extension)
            'filepath': Path(module.get('filepath', '')).name  # Extract filename
        })
    return extracted_modules


In [ ]:
def extract_call_data(calls):
    """
    Extracts data from a list of call dictionaries.

    Args:
        calls (list): A list of dictionaries containing call information.

    Returns:
        list: A list of dictionaries containing extracted call data.
    """
    extracted_calls = []
    for call in calls:
        if not isinstance(call, dict):
            continue  # Skip invalid calls
        extracted_calls.append({
            'category': call.get('category', ''),
            'status': call.get('status', 0),
            'stacktrace': call.get('stacktrace', []),
            'api': call.get('api', ''),
            'return_value': call.get('return_value', 0),
            'arguments': call.get('arguments', {}),
            # Extract additional features from 'arguments' (optional)
            'time': call.get('time', 0),
            'tid': call.get('tid', 0),
            'flags': call.get('flags', {}),
        })
    return extracted_calls

In [ ]:
# Example usage
extracted_data, errors = extract_process_data(processes_sample)

if extracted_data:
    print("Extracted Process Data:")
    for process in extracted_data:
        print(process)

Extracted Process Data:
{'process_path': '^//Windows//System32//lsass.exe', 'pid': 504, 'process_name': 'lsass.exe', 'track': False, 'command_line': '^//Windows//system32//lsass.exe', 'time': 0, 'tid': 2484, 'first_seen': 1705807193.859375, 'ppid': 384, 'type': 'process', 'modules': [{'basename': 'lsass.exe', 'imgsize': 49152, 'filepath': 'lsass.exe'}, {'basename': 'ntdll.dll', 'imgsize': 1740800, 'filepath': 'ntdll.dll'}, {'basename': 'kernel32.dll', 'imgsize': 1175552, 'filepath': 'kernel32.dll'}, {'basename': 'KERNELBASE.dll', 'imgsize': 438272, 'filepath': 'KERNELBASE.dll'}, {'basename': 'msvcrt.dll', 'imgsize': 651264, 'filepath': 'msvcrt.dll'}, {'basename': 'RPCRT4.dll', 'imgsize': 1232896, 'filepath': 'RPCRT4.dll'}, {'basename': 'SspiSrv.dll', 'imgsize': 45056, 'filepath': 'SspiSrv.dll'}, {'basename': 'lsasrv.dll', 'imgsize': 1470464, 'filepath': 'lsasrv.dll'}, {'basename': 'sechost.dll', 'imgsize': 126976, 'filepath': 'sechost.dll'}, {'basename': 'SspiCli.dll', 'imgsize': 15155

### Transformation

In [ ]:
type(extracted_data)

list

In [ ]:
def transform_process_data_to_numeric(process_data):
    """
    Transforms extracted process data into a structured DataFrame.

    Args:
        extracted_data (list): A list containing dictionaries of extracted process data.

    Returns:
        pd.DataFrame: A DataFrame containing the transformed process data.
    """
    # Convert the extracted process data to a DataFrame
    df = pd.DataFrame(process_data)

    # Apply transformations to categorical or textual features

    # Example: TF-IDF vectorization for 'process_path'
    tfidf_vectorizer = TfidfVectorizer()
    process_path_tfidf = tfidf_vectorizer.fit_transform(df['process_path']).toarray()
    process_path_df = pd.DataFrame(process_path_tfidf, columns=tfidf_vectorizer.get_feature_names_out())

    # Combine transformed features into a single DataFrame
    processes_df = pd.concat([df.drop(columns=['process_path']), process_path_df], axis=1)

    return processes_df

In [ ]:
processes_df = transform_process_data_to_numeric(extracted_data)
processes_df.head()


pid process_name  track                     command_line  time   tid  \
0  504    lsass.exe  False  ^//Windows//system32//lsass.exe     0  2484   

     first_seen  ppid     type  \
0  1.705807e+09   384  process   

                                             modules calls  exe  lsass  \
0  [{'basename': 'lsass.exe', 'imgsize': 49152, '...    []  0.5    0.5   

   system32  windows  
0       0.5      0.5

In [ ]:
# Handle command_line, processes, modules
def process_data_to_numeric(process_data):
    # Convert the extracted process data to a DataFrame
    df = pd.DataFrame(process_data)

    # Encode 'command_line' using TF-IDF vectorization
    tfidf_vectorizer = TfidfVectorizer()
    command_line_tfidf = tfidf_vectorizer.fit_transform(df['command_line']).toarray()
    command_line_df = pd.DataFrame(command_line_tfidf, columns=tfidf_vectorizer.get_feature_names_out())

    # Encode 'process_name' using one-hot encoding
    process_name_encoder = OneHotEncoder(sparse=False, handle_unknown='ignore')
    process_name_encoded = process_name_encoder.fit_transform(df[['process_name']])
    process_name_df = pd.DataFrame(process_name_encoded, columns=process_name_encoder.get_feature_names_out())

    # Convert 'track' to binary numeric representation
    df['track'] = df['track'].astype(int)

    # Combine 'modules' data into numeric features
    modules_df = pd.json_normalize(df['modules'])  # Convert list of dictionaries to DataFrame
    # Here you can perform additional processing on 'modules' data if needed, e.g., handling categorical columns or scaling numerical columns

    # Drop original non-numeric columns and concatenate numeric representations
    numeric_df = pd.concat([df.drop(columns=['command_line', 'process_name', 'modules']),
                            command_line_df, process_name_df, modules_df], axis=1)

    return numeric_df

# Example usage:
numeric_df = process_data_to_numeric(processes_df)
numeric_df.head()

/usr/local/lib/python3.10/dist-packages/sklearn/preprocessing/_encoders.py:868: FutureWarning: `sparse` was renamed to `sparse_output` in version 1.2 and will be removed in 1.4. `sparse_output` is ignored unless you leave `sparse` to its default value.
  warnings.warn(


pid  track  time   tid    first_seen  ppid     type calls  exe  lsass  ...  \
0  504      0     0  2484  1.705807e+09   384  process    []  0.5    0.5  ...   

                                                  51  \
0  {'basename': 'WINSTA.dll', 'imgsize': 249856, ...   

                                                  52  \
0  {'basename': 'IPHLPAPI.DLL', 'imgsize': 159744...   

                                                  53  \
0  {'basename': 'WINNSI.DLL', 'imgsize': 45056, '...   

                                                  54  \
0  {'basename': 'netutils.dll', 'imgsize': 49152,...   

                                                  55  \
0  {'basename': 'USERENV.dll', 'imgsize': 122880,...   

                                                  56  \
0  {'basename': 'profapi.dll', 'imgsize': 61440, ...   

                                                  57  \
0  {'basename': 'wshtcpip.dll', 'imgsize': 28672,...   

                                                  58  \
0  {'basename': 'dssenh.dll', 'imgsize': 204800, ...   

                                                  59  \
0  {'basename': 'GPAPI.dll', 'imgsize': 110592, '...   

                                                  60  
0  {'basename': 'monitor-x64.dll', 'imgsize': 226...  

[1 rows x 78 columns]

In [ ]:
numeric_df.columns

Index([                   'pid',                  'track',
                         'time',                    'tid',
                   'first_seen',                   'ppid',
                         'type',                  'calls',
                          'exe',                  'lsass',
                     'system32',                'windows',
                          'exe',                  'lsass',
                     'system32',                'windows',
       'process_name_lsass.exe',                        0,
                              1,                        2,
                              3,                        4,
                              5,                        6,
                              7,                        8,
                              9,                       10,
                             11,                       12,
                             13,                       14,
                             15,                       1

In [ ]:
type(numeric_df)

### TF-IDF

In [55]:
proc_outputs = []
vectorizer = TfidfVectorizer(stop_words=None)
for raw_data in ransom_df['processes'].values:
    raw_vector = vectorizer.fit_transform([raw_data]).toarray()
    proc_outputs.append(raw_vector)

In [56]:
proc_outputs

[array([[0.10955952, 0.0010956 , 0.0010956 , 0.0010956 , 0.0010956 ,
         0.0010956 , 0.0010956 , 0.0010956 , 0.0010956 , 0.11065512,
         0.0010956 , 0.0010956 , 0.0010956 , 0.0010956 , 0.0010956 ,
         0.0010956 , 0.0010956 , 0.0010956 , 0.0010956 , 0.0010956 ,
         0.0010956 , 0.0010956 , 0.0010956 , 0.0010956 , 0.0010956 ,
         0.0010956 , 0.0010956 , 0.0010956 , 0.0010956 , 0.0010956 ,
         0.0010956 , 0.0010956 , 0.0010956 , 0.0010956 , 0.0010956 ,
         0.0010956 , 0.0010956 , 0.0010956 , 0.0010956 , 0.0010956 ,
         0.0010956 , 0.0010956 , 0.0010956 , 0.0010956 , 0.0010956 ,
         0.0010956 , 0.0010956 , 0.0010956 , 0.0010956 , 0.0010956 ,
         0.0010956 , 0.0010956 , 0.0010956 , 0.0010956 , 0.0010956 ,
         0.0010956 , 0.0010956 , 0.0010956 , 0.0010956 , 0.0010956 ,
         0.0010956 , 0.0010956 , 0.0010956 , 0.0010956 , 0.0010956 ,
         0.0010956 , 0.0010956 , 0.0010956 , 0.0010956 , 0.0010956 ,
         0.0010956 , 0.0010956 , 0

## Processes-Tree Data

### Extraction

In [ ]:
def process_children(process_tree_module):
    process_tree_module = process_tree_module.replace('"C:', '^').replace("'", '"').replace(" False", '"false"').replace(" True", '"true"').replace("^", 'C:').replace(' ",', ",").replace("\\", "/")
    process_tree_module = json.loads(process_tree_module)
    process_tree_module = process_tree_module[0]
    data = []

    def traverse(process):
        child_data = {}
        for key, value in process.items():
            if key == 'track':
                child_data['track'] = '1' if value == 'true' else '0'
            elif key == 'process_name':
                child_data['process_name'] = value
            elif key == 'command_line':
                child_data['command_line'] = value
            elif key == 'children':
                child_data['children'] = []
                for child in value:
                    child_data['children'].append(traverse(child))
        return child_data

    data.append(traverse(process_tree_module))
    return data


result = process_children(ransom_df['processtree'])

In [62]:
def process_tree_preprocessing(data):

        datax = data.replace('"C:','^').replace("'",'"').replace(" False",'"false"').replace(" True",'"true"').replace("^",'C:').replace(' ",',",").replace("\\","/")
        data = json.loads(datax)
        output_text = ''
        for raw in data:
            process_tree_module= {}
            process_tree_module['track'] = '1' if raw['track'] == 'true' else '0'
            process_tree_module['process_name'] = raw['process_name']
            if raw['children'] != []:
                 # print(raw['children'])
                process_tree_module['children'] = process_children(raw['children'])



            json_text = json.dumps(process_tree_module,sort_keys=True)
            output_text+=f' {json_text}'

        #hash_obj = hashlib.sha256(output_text.encode()).hexdigest()
        #print(output_text)
        return json.dumps(output_text)


### Transformation

In [ ]:
outputs = []
vectorizer = TfidfVectorizer(stop_words=None)
for index,raw in enumerate(ransom_df['processtree'].values):
    #print(raw[0])
    #print(process_tree_preprocessing(raw[0]))
    raw_processing_data = process_tree_preprocessing(raw[0])
    print(raw_processing_data)

    raw_vector = vectorizer.fit_transform([raw_processing_data]).toarray()
    outputs.append(raw_vector)

In [ ]:
outputs

### TF-IDF

In [64]:
procTree_outputs = []
vectorizer = TfidfVectorizer(stop_words=None)
for raw_data in ransom_df['processtree'].values:
    raw_vector = vectorizer.fit_transform([raw_data]).toarray()
    procTree_outputs.append(raw_vector)

In [65]:
procTree_outputs

[array([[0.12038585, 0.12038585, 0.12038585, 0.12038585, 0.12038585,
         0.12038585, 0.24077171, 0.12038585, 0.12038585, 0.12038585,
         0.12038585, 0.24077171, 0.24077171, 0.48154341, 0.12038585,
         0.24077171, 0.12038585, 0.24077171, 0.24077171, 0.24077171,
         0.24077171, 0.12038585, 0.12038585, 0.24077171, 0.12038585,
         0.12038585, 0.12038585]]),
 array([[0.21320072, 0.21320072, 0.21320072, 0.21320072, 0.21320072,
         0.21320072, 0.42640143, 0.21320072, 0.21320072, 0.42640143,
         0.21320072, 0.21320072, 0.21320072, 0.21320072, 0.21320072,
         0.21320072]]),
 array([[0.12126781, 0.12126781, 0.24253563, 0.12126781, 0.12126781,
         0.12126781, 0.12126781, 0.12126781, 0.12126781, 0.12126781,
         0.24253563, 0.24253563, 0.48507125, 0.12126781, 0.24253563,
         0.12126781, 0.24253563, 0.24253563, 0.24253563, 0.24253563,
         0.12126781, 0.12126781, 0.24253563, 0.12126781, 0.12126781,
         0.12126781]]),
 array([[0.24077171

## Summary Data

### Extraction

In [ ]:
def process_summary(data):
        if data == "{}":
                return json.dumps({'data':''})

        datax = data.replace('"C:','^').replace("'",'"').replace(" False",'"false"').replace(" True",'"true"').replace("^",'C:').replace(' ",',",").replace("\\","/")
        data = json.loads(datax)
        process_data = {}

        if 'file_created' in data.keys():
                process_data['file_created'] = {}
                process_data['file_created']['len'] = len(data['file_created'])
                process_data['file_created']['pathes']= list(([x.split(":/")[0] for x in data['file_created']]))

        if 'file_recreated' in data.keys():

                process_data['file_recreated'] = {
                }
                process_data['file_recreated']['len']= len(data['file_recreated'])
                process_data['file_recreated']['paths']= list(([x.split("\\")[0] for x in data['file_recreated']]))

        if 'dll_loaded' in data.keys():

                process_data['dll_loaded'] = {}
                process_data['dll_loaded']['paths'] = list(([x for x in data['dll_loaded']]))

        if 'file_opened' in data.keys():
                process_data['file_opened'] = {}
                process_data['file_opened']['files'] = list(([x.split("//")[-1] for x in data['file_opened'] ]) )

        if 'regkey_opened' in data.keys():
                process_data['regkey_opened'] = {}
                process_data['regkey_opened']['files'] = list(([x.split("//")[-1] for x in data['regkey_opened'] ]) )


        if 'file_written' in data.keys():
                process_data['file_written'] = {}
                process_data['file_written']['files'] = list(([x.split("//")[-1] for x in data['file_written'] ]) )

        if 'file_deleted' in data.keys():
                process_data['file_deleted'] = {}
                process_data['file_deleted']['files'] = list(([x.split("//")[-1] for x in data['file_deleted'] ]) )

        if 'file_failed' in data.keys():
                process_data['file_failed'] = {}
                process_data['file_failed']['files'] = list(([x.split("//")[-1] for x in data['file_failed'] ]) )

        if 'guid' in data.keys():
                process_data['guid'] = data['guid']

        if 'file_read' in data.keys():
                process_data['file_read'] = {}
                process_data['file_read']['files'] = list([x.split("//")[-1] for x in data['file_read'] ])

        if 'regkey_read' in data.keys():
                process_data['regkey_read'] = {}
                process_data['regkey_read']['files'] = list([x.split("//")[-1] for x in data['regkey_read'] ])


        return json.dumps(process_data)

In [ ]:
df_ransom['summary'].values[3]

### Transformation

In [ ]:
vectorizer = TfidfVectorizer(stop_words=None)
output = process_summary(df_job['summary'].values[6])
print(output)
raw_vector = vectorizer.fit_transform([output]).toarray()


In [ ]:
outputs = []
vectorizer = TfidfVectorizer(stop_words=None)
for index,raw in enumerate(df_job.values):
    #print(raw[0])
    #print(process_tree_preprocessing(raw[0]))
    raw_processing_data = process_summary(raw[1])
    print('output',raw_processing_data)
    #print('epoch',index)
    raw_vector = vectorizer.fit_transform([raw_processing_data]).toarray()
    outputs.append(raw_vector)

In [ ]:
outputs

### TF-IDF

In [95]:
ransom_df['summary'][1] = ransom_df['summary'][1].replace('{N}','{NAN}')
ransom_df['summary']

0    {'regkey_read': ['HKEY_LOCAL_MACHINE\\SOFTWARE...
1                                                {NAN}
2    {'file_created': ['C:\\Users\\Administrator\\D...
3    {'file_recreated': ['\\Device\\KsecDD'], 'regk...
4    {'regkey_read': ['HKEY_LOCAL_MACHINE\\SYSTEM\\...
5    {'file_recreated': ['\\??\\MountPointManager']...
6    {'file_recreated': ['\\Device\\KsecDD'], 'regk...
7    {'dll_loaded': ['kernel32', 'api-ms-win-core-l...
8    {'file_opened': ['C:\\Windows\\System32\\en-US...
Name: summary, dtype: object

In [96]:
summary_outputs = []
vectorizer = TfidfVectorizer(stop_words=None)
for raw_data in ransom_df['summary'].values:
    raw_vector = vectorizer.fit_transform([raw_data]).toarray()
    summary_outputs.append(raw_vector)

In [97]:
v

[array([[0.25, 0.25, 0.5 , 0.25, 0.25, 0.25, 0.25, 0.25, 0.25, 0.25, 0.25,
         0.25, 0.25]]),
 array([[1.]]),
 array([[0.00110709, 0.00081575, 0.00565199, ..., 0.00011654, 0.00011654,
         0.00011654]]),
 array([[0.09365858, 0.37463432, 0.37463432, 0.09365858, 0.09365858,
         0.09365858, 0.09365858, 0.09365858, 0.09365858, 0.18731716,
         0.09365858, 0.09365858, 0.09365858, 0.18731716, 0.09365858,
         0.46829291, 0.09365858, 0.18731716, 0.09365858, 0.18731716,
         0.09365858, 0.09365858, 0.09365858, 0.37463432, 0.09365858,
         0.18731716, 0.18731716]]),
 array([[0.33333333, 0.22222222, 0.22222222, 0.33333333, 0.11111111,
         0.11111111, 0.22222222, 0.11111111, 0.11111111, 0.22222222,
         0.11111111, 0.33333333, 0.11111111, 0.33333333, 0.22222222,
         0.11111111, 0.11111111, 0.22222222, 0.22222222, 0.33333333]]),
 array([[0.07287824, 0.03643912, 0.00728782, 0.00728782, 0.00728782,
         0.00728782, 0.00728782, 0.02186347, 0.00728782, 0

## Image Generation

In [126]:
import cv2
import numpy as np

# Function to create grayscale image from array
def create_grayscale_image(array, image_shape=(256, 256)):
    # Resize array to match image dimensions
    resized_array = cv2.resize(array, image_shape[::-1])

    # Normalize array values between 0 and 255
    normalized_array = ((resized_array - resized_array.min()) / (resized_array.max() - resized_array.min())) * 255

    # Convert to uint8
    image_data = normalized_array.astype(np.uint8)

    return image_data

# Directory to store the images
output_folder = "combined_images"
os.makedirs(output_folder, exist_ok=True)

# Iterate over each pair of arrays in proc_outputs and gen_outputs
for i, (gen_array, apiStats_array, proc_array, procTree_array, summary_array) in enumerate(zip(gen_outputs, apiStats_outputs,proc_outputs, procTree_outputs, summary_outputs)):
    # Combine arrays
    combined_array = np.concatenate((gen_array, apiStats_array, proc_array, procTree_array, summary_array), axis=1)

    # Create grayscale image from combined array
    image_data = create_grayscale_image(combined_array)

    # Save image as PNG file
    filename = os.path.join(output_folder, f"combined_image_{i}.png")
    cv2.imwrite(filename, image_data)
    print(f"Image saved: {filename}")


Image saved: combined_images/combined_image_0.png
Image saved: combined_images/combined_image_1.png
Image saved: combined_images/combined_image_2.png
Image saved: combined_images/combined_image_3.png
Image saved: combined_images/combined_image_4.png
Image saved: combined_images/combined_image_5.png
Image saved: combined_images/combined_image_6.png
Image saved: combined_images/combined_image_7.png
Image saved: combined_images/combined_image_8.png


# Test

In [ ]:
import pandas as pd
from sklearn.feature_extraction.text import TfidfVectorizer

def transform_generic(data):
    # Example transformation for the 'generic' column
    return data.apply(lambda x: len(x))  # Replace this with your actual transformation logic

def transform_apistats(data):
    # Example transformation for the 'apistats' column
    return data.apply(lambda x: x * 2)  # Replace this with your actual transformation logic

def transform_processes(data):
    # Example transformation for the 'processes' column
    return data.apply(lambda x: x.upper())  # Replace this with your actual transformation logic

def transform_processtree(data):
    # Example transformation for the 'processtree' column
    return data.apply(lambda x: x.lower())  # Replace this with your actual transformation logic

def transform_summary(data):
    # Example transformation for the 'summary' column
    return data.apply(lambda x: x.split())  # Replace this with your actual transformation logic

def transform_columns(dataframe, column_transformations):
    """
    Transform columns in a DataFrame based on provided transformations.

    Args:
        dataframe (pandas.DataFrame): The DataFrame containing the columns to transform.
        column_transformations (dict): A dictionary where keys are column names and values are transformation functions.

    Returns:
        pandas.DataFrame: A new DataFrame containing the transformed columns.
    """
    transformed_data = {}

    # Iterate over each column and apply the corresponding transformation
    for column, transformation in column_transformations.items():
        transformed_data[column] = transformation(dataframe[column])

    # Create a new DataFrame from the transformed data
    transformed_df = pd.DataFrame(transformed_data)

    return transformed_df

# Define transformations for each column
column_transformations = {
    'generic': transform_generic,
    'apistats': transform_apistats,
    'processes': transform_processes,
    'processtree': transform_processtree,
    'summary': transform_summary
}

# Apply transformations to ransom_df
transformed_df = transform_columns(ransom_df, column_transformations)
transformed_df

generic                                           apistats  \
0      618  {'664': {'CreateToolhelp32Snapshot': 1, 'LdrUn...   
1      156                                               {}{}   
2   974413  {'1756': {'GetNativeSystemInfo': 1, 'DeviceIoC...   
3     1004  {'2424': {'LdrUnloadDll': 2, 'DeviceIoControl'...   
4      763  {'2684': {'GetForegroundWindow': 8, 'NtAllocat...   
5    11151  {'2836': {'LdrUnloadDll': 3, 'CoUninitialize':...   
6    13159  {'2316': {'NtDuplicateObject': 1, 'DeviceIoCon...   
7  1117475  {'2232': {'NtDuplicateObject': 7, 'LdrUnloadDl...   
8     1717  {'800': {'LdrUnloadDll': 1, 'NtDeviceIoControl...   

                                           processes  \
0  [{'PROCESS_PATH': 'C:\\WINDOWS\\SYSTEM32\\LSAS...   
1  [{'PROCESS_PATH': 'C:\\WINDOWS\\SYSTEM32\\LSAS...   
2  [{'PROCESS_PATH': 'C:\\WINDOWS\\SYSTEM32\\LSAS...   
3  [{'PROCESS_PATH': 'C:\\WINDOWS\\SYSTEM32\\LSAS...   
4  [{'PROCESS_PATH': 'C:\\WINDOWS\\SYSTEM32\\LSAS...   
5  [{'PROCESS_PATH': 'C:\\WINDOWS\\SYSTEM32\\LSAS...   
6  [{'PROCESS_PATH': 'C:\\WINDOWS\\SYSTEM32\\LSAS...   
7  [{'PROCESS_PATH': 'C:\\WINDOWS\\SYSTEM32\\LSAS...   
8  [{'PROCESS_PATH': 'C:\\WINDOWS\\SYSTEM32\\LSAS...   

                                         processtree  \
0  [{'track': false, 'pid': 516, 'process_name': ...   
1  [{'track': false, 'pid': 504, 'process_name': ...   
2  [{'track': false, 'pid': 516, 'process_name': ...   
3  [{'track': false, 'pid': 512, 'process_name': ...   
4  [{'track': false, 'pid': 508, 'process_name': ...   
5  [{'track': false, 'pid': 504, 'process_name': ...   
6  [{'track': false, 'pid': 508, 'process_name': ...   
7  [{'track': false, 'pid': 508, 'process_name': ...   
8  [{'track': false, 'pid': 500, 'process_name': ...   

                                             summary  
0  [{'regkey_read':, ['HKEY_LOCAL_MACHINE\\SOFTWA...  
1                                               [{}]  
2  [{'file_created':, ['C:\\Users\\Administrator\...  
3  [{'file_recreated':, ['\\Device\\KsecDD'],, 'r...  
4  [{'regkey_read':, ['HKEY_LOCAL_MACHINE\\SYSTEM...  
5  [{'file_recreated':, ['\\??\\MountPointManager...  
6  [{'file_recreated':, ['\\Device\\KsecDD'],, 'r...  
7  [{'dll_loaded':, ['kernel32',, 'api-ms-win-cor...  
8  [{'file_opened':, ['C:\\Windows\\System32\\en-...

In [ ]:
# Define textual columns
text_features = ['generic', 'apistats', 'processes', 'processtree', 'summary']

In [ ]:
transformed_df['Label'] = ransom_df['Directory_Label']

In [ ]:
import cv2
import numpy as np
from sklearn.feature_extraction.text import TfidfVectorizer
from skimage.transform import resize

# Iterate over each row in the dataframe
for index, row in transformed_df.iterrows():
    # Handle textual columns
    vectorizer = TfidfVectorizer(stop_words=None)
    encoded_texts = []
    for feature in text_features:
        text = row[feature]
        if isinstance(text, str) and text.strip():  # Check if the text is not empty or contains only whitespace
            try:
                # Use TF-IDF vectorization for each textual feature
                encoded_text = vectorizer.fit_transform([text]).toarray()
                encoded_texts.append(encoded_text)
            except ValueError:
                print(f"Skipping feature {feature} for index {index} due to ValueError.")
                continue

    encoded_data = np.concatenate(encoded_texts, axis=1)

    # Create normalized grayscale image
    image_width = 256
    image_height = 256
    image = np.zeros((image_height, image_width), dtype=np.uint8)
    encoded_data_normalized = (encoded_data - encoded_data.min()) / (encoded_data.max() - encoded_data.min())

    # Resize the encoded data to match image dimensions
    resized_data = resize(encoded_data_normalized, (image_height, image_width))

    # Assign the resized data to the image
    image[:, :] = (resized_data * 255).astype(np.uint8)

    # Get the label value from the dataframe
    label_value = row['Label']  # Assuming 'label' is the name of the column containing label values

    # Save the image with a filename based on the label value
    filename = f"data_image_{label_value}.png"
    cv2.imwrite(filename, image)
    print(f"Image saved: {filename}")


Image saved: data_image_8Base.png
Skipping feature apistats for index 1 due to ValueError.
Image saved: data_image_BianLian.png
Image saved: data_image_BlackBasta.png
Image saved: data_image_BlackCat.png
Image saved: data_image_CL0P.png
Image saved: data_image_MedusaLocker.png
Image saved: data_image_NoEscape.png
Image saved: data_image_Play.png
Image saved: data_image_Royal.png


In [ ]:
# import numpy as np
# from PIL import Image

# # Assuming proc_outputs and gen_outputs contain the transformed arrays for each sample
# # Convert lists of arrays to arrays
# proc_arrays = [np.array(item) for item in proc_outputs]
# gen_arrays = [np.array(item) for item in gen_outputs]

# # Ensure all arrays have the same shape
# max_length = max(arr.shape[-1] for arr in proc_arrays + gen_arrays)  # Use -1 to access last dimension

# # Reshape arrays to have compatible shapes (adjust for actual dimensions if needed)
# proc_arrays_reshaped = [arr.reshape(arr.shape[0], max_length) for arr in proc_arrays]
# gen_arrays_reshaped = [arr.reshape(arr.shape[0], max_length) for arr in gen_arrays]

# # Combine arrays into a single array for processing
# combined_arrays = np.concatenate(proc_arrays_reshaped + gen_arrays_reshaped, axis=0)

# # Normalize combined arrays
# combined_normalized = (combined_arrays - combined_arrays.min()) / (combined_arrays.max() - combined_arrays.min())

# # Convert to grayscale image
# combined_image = Image.fromarray((combined_normalized * 255).astype(np.uint8), mode='L')

# # Display or save the combined image
# combined_image.show()


In [ ]:
# import numpy as np

# # Shapes of the arrays
# proc_shapes = [(1, 279), (1, 204), (1, 3470), (1, 266), (1, 275), (1, 389), (1, 312), (1, 868), (1, 300)]
# gen_shapes = [(1, 36), (1, 14), (1, 8948), (1, 50), (1, 44), (1, 257), (1, 266), (1, 4088), (1, 88)]

# # Create sample data for demonstration
# proc_arrays = [np.random.rand(*shape) for shape in proc_shapes]
# gen_arrays = [np.random.rand(*shape) for shape in gen_shapes]

# # Reshape arrays to have compatible shapes
# proc_arrays_resized = [arr.reshape((arr.shape[0], 1, arr.shape[1])) for arr in proc_arrays]
# gen_arrays_resized = [arr.reshape((arr.shape[0], 1, arr.shape[1])) for arr in gen_arrays]

# # Concatenate arrays along a new axis
# combined_arrays = np.concatenate(proc_arrays_resized + gen_arrays_resized, axis=1)

# # Display the shape of the combined array
# print("Combined array shape:", combined_arrays.shape)
